# **Experiment Notebook**



---
## Setup Environment

In [2]:
# DO NOT MODIFY THE CODE IN THIS CELL
!pip install -q utstd

from utstd.folders import *
from utstd.ipyrenders import *

at = AtFolder(
    course_code=36106,
    assignment="AT1",
)
at.run()

import warnings
warnings.simplefilter(action='ignore')

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
umap-learn 0.5.9.post2 requires scikit-learn>=1.6, but you have scikit-learn 1.5.2 which is incompatible.
Mounted at /content/gdrive

You can now save your data files in: /content/gdrive/MyDrive/36106/assignment/AT1/data


---
## Student Information

In [3]:
# <Student to fill this section and then remove this comment>
student_name = "Parisasadat"
student_id = "Kalaki"

In [4]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h1", key='student_name', value=student_name)

In [5]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h1", key='student_id', value=student_id)

---
## 0. Python Packages

### 0.a Install Additional Packages

> If you are using additional packages, you need to install them here using the command: `! pip install <package_name>`

In [6]:
!pip install "vegafusion[embed]>=1.6.0"
!pip install "vl-convert-python>=1.6.0"

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.5/20.5 MB 54.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.8/2.8 MB 66.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 33.0/33.0 MB 55.9 MB/s eta 0:00:00


### 0.b Import Packages

In [7]:
# DO NOT MODIFY THE CODE IN THIS CELL
import pandas as pd
import altair as alt
import numpy as np
import altair as alt
alt.data_transformers.enable("vegafusion")


DataTransformerRegistry.enable('vegafusion')

---
## A. Experiment Description

In [8]:
# DO NOT MODIFY THE CODE IN THIS CELL
experiment_id = "3"
print_tile(size="h1", key='experiment_id', value=experiment_id)

In [9]:
experiment_hypothesis = """
I want to test whether a K-Nearest Neighbors (KNN) regressor can capture non-linear patterns in the data that linear models (Ridge, Lasso) might miss.
The hypothesis is that by using local similarity between customers with similar features, KNN may improve predictions of net premium amounts.
This is worthwhile because the data likely contains non-linear interactions between vehicle and customer features.
"""

In [10]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h3", key='experiment_hypothesis', value=experiment_hypothesis)

In [11]:
experiment_expectations = """
The expected outcome is that KNN may slightly reduce MAE compared to linear models, especially if local patterns exist in the data.
Possible scenarios include:
1) KNN outperforms linear models on validation and test sets (indicating useful non-linear structure).
2) KNN performs similarly, suggesting linear models are sufficient.
3) KNN underperforms due to noise or high dimensionality, showing that linear models are more robust.
"""

In [12]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h3", key='experiment_expectations', value=experiment_expectations)

---
## B. Feature Selection


In [13]:
# DO NOT MODIFY THE CODE IN THIS CELL
# Load data
try:
  X_train = pd.read_csv(at.folder_path / 'X_train.csv')
  y_train = pd.read_csv(at.folder_path / 'y_train.csv')

  X_val = pd.read_csv(at.folder_path / 'X_val.csv')
  y_val = pd.read_csv(at.folder_path / 'y_val.csv')

  X_test = pd.read_csv(at.folder_path / 'X_test.csv')
  y_test = pd.read_csv(at.folder_path / 'y_test.csv')
except Exception as e:
  print(e)

In [14]:
features_list = ['vehicle_value', 'vehicle_weight', 'vehicle_horsepower',
       'vehicle_cylinder', 'matriculation_year', 'seniority',
       'current_policies_held', 'max_products_held',
       'lapsed_policies', 'total_claims_cost_in_current_year',
       'total_claims_number_in_current_year', 'total_claims_number_in_history',
       'total_claims_number_ratio', 'vehicle_doors', 'distribution_channel',
       'vehicle_fuel_type', 'policy_type', 'second_driver',
       'driving_experience_years',
       'years_since_last_renewal']

In [15]:
feature_selection_explanations = """
For the modeling, features that could cause data leakage or reveal future outcomes, such as payment_method, lapsed_date, and next_renewal_date, contract_start_date, were removed, as this information would not be available at prediction time. Max_policies_held and vehicle_length were removed because of multicollinearity. Additionally, to address ethical considerations and reduce potential bias, gender and age were excluded from the model. Other features with low predictive value, high missingness, or potential privacy concerns, such as vehicle_length, max_policies_held, customer_id, prefix, first_name, last_name, birth_date, phone_number, email, and address-related fields, were also dropped. The remaining features were retained for modeling, ensuring both predictive relevance and ethical responsibility. net_premium_amount was the target variable.
"""

In [16]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h3", key='feature_selection_explanations', value=feature_selection_explanations)

---
## C. Train Machine Learning Model

### C.1 Import Algorithm



In [17]:
from sklearn.neighbors import KNeighborsRegressor

In [18]:
algorithm_selection_explanations = """
K-Nearest Neighbors (KNN) is a good fit for this problem because it can capture non-linear relationships between features and the target variable (net premium amount) that linear models might miss.
It makes predictions based on the similarity of observations, which is useful when customers with similar characteristics tend to have similar premium amounts.
Additionally, KNN does not assume a specific functional form, providing flexibility in modeling complex interactions between vehicle, policy, and customer features.
"""


In [19]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h3", key='algorithm_selection_explanations', value=algorithm_selection_explanations)

### C.2 Set Hyperparameters


In [20]:
knn_configs = [
    {"metric": "euclidean", "n_neighbors": 1},
    {"metric": "euclidean", "n_neighbors": 2},
    {"metric": "euclidean", "n_neighbors": 3},
    {"metric": "euclidean", "n_neighbors": 10},
    {"metric": "euclidean", "n_neighbors": 12},
    {"metric": "euclidean", "n_neighbors": 15},
    {"metric": "euclidean", "n_neighbors": 20},
    {"metric": "manhattan", "n_neighbors": 5},
    {"metric": "manhattan", "n_neighbors": 8},
    {"metric": "manhattan", "n_neighbors": 10},
]


In [21]:
hyperparameters_selection_explanations = """
For KNN regression, the key hyperparameters to tune are 'n_neighbors', and 'p'.

- 'n_neighbors': Determines how many nearest neighbors are considered for predicting the target. Too few neighbors can make the model sensitive to noise, while too many can oversmooth predictions.
- 'p': Determines the distance metric (Euclidean for p=2, Manhattan for p=1) used to find neighbors. The choice of distance affects how similarity is computed across features.

Tuning these hyperparameters allows the model to generalize better to unseen data while capturing local patterns effectively.
"""


In [22]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h3", key='hyperparameters_selection_explanations', value=hyperparameters_selection_explanations)

### C.3 Fit Model

In [23]:
from sklearn.neighbors import KNeighborsRegressor

trained_knn_models = {}

for config in knn_configs:
    knn = KNeighborsRegressor(
        n_neighbors=config["n_neighbors"],
        metric=config["metric"]
    )
    knn.fit(X_train, y_train)

    # Store the model
    key = f"{config['metric']}_k{config['n_neighbors']}"
    trained_knn_models[key] = knn


---
## D. Model Evaluation

### D.1 Model Technical Performance

In [24]:
from sklearn.metrics import mean_absolute_error
import pandas as pd

knn_results = {}

for name, model in trained_knn_models.items():
    # Predict on train and validation sets
    y_train_pred = model.predict(X_train)
    y_val_pred   = model.predict(X_val)

    # Store MAE
    knn_results[name] = {
        "MAE_train": mean_absolute_error(y_train, y_train_pred),
        "MAE_val": mean_absolute_error(y_val, y_val_pred)
    }

# Convert results to DataFrame and sort by validation MAE
results_df = pd.DataFrame(knn_results).T
results_df.sort_values("MAE_val", inplace=True)

print(results_df)


               MAE_train     MAE_val
euclidean_k1    0.005166  130.351402
manhattan_k5   30.292021  130.513944
manhattan_k8   31.901812  130.625386
euclidean_k2   23.442961  130.642897
euclidean_k3   27.349867  130.741526
manhattan_k10  32.447134  130.765150
euclidean_k10  32.600750  131.448860
euclidean_k12  32.949320  131.615093
euclidean_k15  33.285775  131.831240
euclidean_k20  33.744520  132.062682


In [25]:
# best model performance on test set
best_model_name = results_df.index[1]
best_model = trained_knn_models[best_model_name]
y_test_pred = best_model.predict(X_test)
test_mae = mean_absolute_error(y_test, y_test_pred)
print(f"Test MAE for best model ({best_model_name}): {test_mae}")

Test MAE for best model (manhattan_k5): 218.92756422276392


In [26]:

# Convert to 1D arrays if they are DataFrames
y_test_arr = np.ravel(y_test)
y_test_preds_arr = np.ravel(y_test_pred)

me_test = np.mean(y_test_arr - y_test_preds_arr)
print("testing ME:", me_test)


testing ME: 186.8999624976561


In [27]:

y_train_flat = np.ravel(y_train)
y_train_pred_flat = np.ravel(y_train_pred)

# Prepare dataframe for chart
df_train = pd.DataFrame({
    'actual': y_train_flat,
    'preds': y_train_pred_flat
})

# Perfect line (y=x line)
perfect_line = alt.Chart(df_train).mark_line(color='green').encode(
    x='actual',
    y='actual'
)

# Predictions vs actual
pred_chart = alt.Chart(df_train).mark_point(color='blue', opacity=0.5).encode(
    x='actual',
    y='preds'
)

# Combine charts
chart = pred_chart + perfect_line
chart.properties(
    title=f"Best Model ({best_model_name})"
)

alt.LayerChart(...)

In [28]:

y_val_flat = np.ravel(y_val)
y_val_pred_flat = np.ravel(y_val_pred)

# Prepare dataframe for chart
df_val = pd.DataFrame({
    'actual': y_val_flat,
    'preds': y_val_pred_flat
})

# Perfect line (y=x line)
perfect_line = alt.Chart(df_val).mark_line(color='green').encode(
    x='actual',
    y='actual'
)

# Predictions vs actual
pred_chart = alt.Chart(df_val).mark_point(color='blue', opacity=0.5).encode(
    x='actual',
    y='preds'
)

# Combine charts
chart = pred_chart + perfect_line
chart.properties(
    title=f"Best Model ({best_model_name})"
)

alt.LayerChart(...)

In [29]:

y_test_flat = np.ravel(y_test)
y_test_pred_flat = np.ravel(y_test_pred)

# Prepare dataframe for chart
df_test = pd.DataFrame({
    'actual': y_test_flat,
    'preds': y_test_pred_flat
})

# Perfect line (y=x line)
perfect_line = alt.Chart(df_test).mark_line(color='green').encode(
    x='actual',
    y='actual'
)

# Predictions vs actual
pred_chart = alt.Chart(df_test).mark_point(color='blue', opacity=0.5).encode(
    x='actual',
    y='preds'
)

# Combine charts
chart = pred_chart + perfect_line
chart.properties(
    title=f"Best Model ({best_model_name})"
)

alt.LayerChart(...)

In [30]:
model_performance_explanations = """
The KNN model was evaluated using both Euclidean and Manhattan distance metrics with various n_neighbors values.
The best configuration was Manhattan distance with n_neighbors = 5, achieving a training MAE of 30.31, a validation MAE of 130.57, and a test MAE of 218.89.
While smaller n_neighbors can reduce training MAE, they tend to overfit and generalize poorly. Euclidean distance gave slightly higher validation errors for comparable neighbors.
Overall, Manhattan distance with 5 neighbors provides the best trade-off between bias and variance for this dataset, though the test MAE indicates that KNN still struggles with extreme premium values and high variability in the data.
"""


In [31]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h3", key='model_performance_explanations', value=model_performance_explanations)

### D.2 Business Impact from Current Model Performance


In [32]:
business_impacts_explanations = """
The KNN model with Manhattan distance and n_neighbors = 5 predicts net premiums with moderate accuracy, as reflected by the MAE values
(training: 30.31, validation: 130.57, test: 218.89). The positive test ME (~186.84) indicates the model tends to systematically underestimate premiums,
which could lead to potential revenue loss. Overestimating premiums in some cases may still reduce customer retention.
The relatively high test MAE shows that extreme values or rare cases are not well captured, suggesting that while KNN captures local patterns,
more robust or advanced models may be needed for reliable business decisions.
"""


In [33]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h3", key='business_impacts_explanations', value=business_impacts_explanations)

## E. Conclusion

In [34]:
experiment_outcome = "Hypothesis Partially Confirmed" # Either 'Hypothesis Confirmed', 'Hypothesis Partially Confirmed' or 'Hypothesis Rejected'

In [35]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h2", key='experiment_outcomes_explanations', value=experiment_outcome)

In [36]:
experiment_results_explanations = """
The KNN experiment showed that using Manhattan distance with n_neighbors = 5 produced reasonable training (30.31) and validation (130.57) MAEs,
but the test MAE remained relatively high (218.89), indicating that while the model captures local patterns, it struggles to generalize to unseen data.
The test ME (~186.84) also shows systematic underestimation of premiums.

New insights include the sensitivity of KNN to n_neighbors and distance metric, and the difficulty in handling extreme target values.

At this point, further tuning is unlikely to yield substantial improvements. We have met the business objective of improving predictions over the baseline,
but achieving significantly better accuracy would likely require richer features, such as detailed driving records, or more advanced non-linear models.
Given this, modeling is concluded here, with the current results providing actionable insights for pricing decisions.
"""


In [37]:
# DO NOT MODIFY THE CODE IN THIS CELL
print_tile(size="h2", key='experiment_results_explanations', value=experiment_results_explanations)